In [36]:
%pip install numpy spektral tensorflow -q
import tensorflow as tf
import numpy as np
import spektral
from spektral.datasets.citation import Citation
from tqdm import tqdm

Note: you may need to restart the kernel to use updated packages.


In [66]:
dataset = Citation('pubmed', normalize_x=True)
dataset = Citation('pubmed', normalize_x=True, transforms=[LayerPreprocess(GCNConv)])

adj = dataset.graphs[0].a.todense()
features = dataset.graphs[0].x
labels = dataset.graphs[0].y
train_mask, val_mask, test_mask = dataset.mask_tr, dataset.mask_va, dataset.mask_te

def masked_softmax_cross_entropy(logits, labels, mask):
  loss = tf.nn.softmax_cross_entropy_with_logits(labels=labels, logits=logits)
  mask = tf.cast(mask, dtype=tf.float32)
  mask /= tf.reduce_mean(mask)
  loss *= mask
  return tf.reduce_mean(loss)

def masked_accuracy(logits, labels, mask):
  correct_preds = tf.equal(tf.argmax(logits, 1), tf.argmax(labels, 1))
  accuracy = tf.cast(correct_preds, dtype=tf.float32)
  mask = tf.cast(mask, dtype=tf.float32)
  mask /= tf.reduce_mean(mask)
  accuracy *= mask
  return tf.reduce_mean(accuracy)

def gnn_fn(features, adj, transform, activation):
  seq_fts =  transform(features)
  ret_fts = tf.matmul(adj, seq_fts)
  return activation(ret_fts)

def train(features, adj, gnn_fn, units, epochs, lr=0.01):
  lyr_1 = tf.keras.layers.Dense(units)
  lyr_2 = tf.keras.layers.Dense(3)
   
  def gnn_net(features, adj):
    hidden = gnn_fn(features, adj, lyr_1, tf.nn.relu)
    logits = gnn_fn(hidden, adj, lyr_2, tf.identity)
    return logits
  
  optimizer = tf.keras.optimizers.Adam(learning_rate=lr)
  best_accuracy = 0.0
  
  for epoch in range(epochs+1):
    with tf.GradientTape() as t:
      logits = gnn_net(features, adj)
      loss = masked_softmax_cross_entropy(logits, labels, train_mask)

    variables = t.watched_variables()
    grads = t.gradient(loss, variables)
    optimizer.apply_gradients(zip(grads, variables))

    logits = gnn_net(features, adj)
    val_accuracy = masked_accuracy(logits, labels, val_mask)
    test_accuracy = masked_accuracy(logits, labels, test_mask)
    
    if val_accuracy > best_accuracy:
      best_accuracy = val_accuracy
      print(f'epoch: {epoch},'
            f'train_loss: {loss.numpy()},'
            f'val_acc: {val_accuracy.numpy()},'
            f'test_acc: {test_accuracy.numpy()}')

train(features, adj, gnn_fn, 32, 20, 0.01)

Pre-processing node features


/usr/local/Caskroom/miniforge/base/envs/py3/lib/python3.9/site-packages/scipy/sparse/_index.py:125: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


Pre-processing node features
epoch: 0,train_loss: 1.0980415344238281,val_acc: 0.4699999988079071,test_acc: 0.48900002241134644
epoch: 1,train_loss: 1.0857902765274048,val_acc: 0.531999945640564,test_acc: 0.5269998908042908
epoch: 5,train_loss: 1.0279830694198608,val_acc: 0.5459999442100525,test_acc: 0.5679998993873596
epoch: 6,train_loss: 1.0107402801513672,val_acc: 0.6380000710487366,test_acc: 0.6259998679161072
epoch: 7,train_loss: 0.9920498132705688,val_acc: 0.6820001006126404,test_acc: 0.6719997525215149
epoch: 8,train_loss: 0.9725067615509033,val_acc: 0.7120000720024109,test_acc: 0.6989997625350952
epoch: 9,train_loss: 0.9518073201179504,val_acc: 0.724000096321106,test_acc: 0.7109997868537903
epoch: 10,train_loss: 0.929932177066803,val_acc: 0.736000120639801,test_acc: 0.7179997563362122
epoch: 14,train_loss: 0.8337627053260803,val_acc: 0.7380000948905945,test_acc: 0.7209997773170471
epoch: 15,train_loss: 0.8073488473892212,val_acc: 0.7420001029968262,test_acc: 0.7239997982978821


In [68]:
# on identity train(features, tf.eye(adj.shape[0]), gnn_fn, 32, 20, 0.01)

# normalize adj by degree
deg = tf.reduce_sum(adj, axis=-1)
train(features, adj / deg, gnn_fn, 32, 20, 0.01)

epoch: 0,train_loss: 1.0996336936950684,val_acc: 0.5119999647140503,test_acc: 0.4919999837875366
epoch: 2,train_loss: 1.073289394378662,val_acc: 0.5379999876022339,test_acc: 0.5219999551773071
epoch: 3,train_loss: 1.0569909811019897,val_acc: 0.6000000238418579,test_acc: 0.5999998450279236
epoch: 4,train_loss: 1.0379494428634644,val_acc: 0.6700000166893005,test_acc: 0.6739997863769531
epoch: 5,train_loss: 1.0155421495437622,val_acc: 0.7160000801086426,test_acc: 0.7109997868537903
epoch: 6,train_loss: 0.9916436672210693,val_acc: 0.7280001044273376,test_acc: 0.7139998078346252
epoch: 9,train_loss: 0.9153128266334534,val_acc: 0.7300000786781311,test_acc: 0.7069997787475586
epoch: 11,train_loss: 0.8576377034187317,val_acc: 0.7320001125335693,test_acc: 0.711999773979187
epoch: 12,train_loss: 0.8269254565238953,val_acc: 0.7380000948905945,test_acc: 0.714999794960022
epoch: 13,train_loss: 0.7955628037452698,val_acc: 0.7440001368522644,test_acc: 0.7159997820854187
epoch: 15,train_loss: 0.731915

In [69]:
# thomas gibb in graph conv networks: normalize by 1/sqrt(deg)

norm_deg = tf.linalg.diag(1.9 / tf.sqrt(deg))
norm_adj = tf.matmul(norm_deg, tf.matmul(adj, norm_deg))
train(features, norm_adj, gnn_fn, 32, 200, 0.01)

KeyboardInterrupt: 

Another impl:

In [39]:
"""
This example implements the experiments on citation networks from the paper:
Semi-Supervised Classification with Graph Convolutional Networks (https://arxiv.org/abs/1609.02907)
Thomas N. Kipf, Max Welling
"""
import numpy as np
import tensorflow as tf
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.losses import CategoricalCrossentropy
from tensorflow.keras.optimizers import Adam

from spektral.data.loaders import SingleLoader
from spektral.layers import GCNConv
from spektral.models.gcn import GCN
from spektral.transforms import LayerPreprocess

learning_rate = .01
epochs = 100
patience = 10

# We convert the binary masks to sample weights so that we can compute the
# average loss over the nodes (following original implementation by
# Kipf & Welling)
def mask_to_weights(mask):
    return mask.astype(np.float32) / np.count_nonzero(mask)


weights_tr, weights_va, weights_te = (
    mask_to_weights(mask)
    for mask in (dataset.mask_tr, dataset.mask_va, dataset.mask_te)
)

# define the model
model = GCN(n_labels=dataset.n_labels, n_input_channels=dataset.n_node_features)
model.compile(
    optimizer=Adam(learning_rate),
    loss=CategoricalCrossentropy(reduction="sum"),
    weighted_metrics=["acc"],
)

loader_tr = SingleLoader(dataset, sample_weights=weights_tr)
loader_va = SingleLoader(dataset, sample_weights=weights_va)
loader_te = SingleLoader(dataset, sample_weights=weights_te)

# Train
model.fit(
    loader_tr.load(),
    steps_per_epoch=loader_tr.steps_per_epoch,
    validation_data=loader_va.load(),
    validation_steps=loader_va.steps_per_epoch,
    epochs=epochs,
    callbacks=[EarlyStopping(patience=patience, restore_best_weights=True)],
)

# Evaluate
eval_results = model.evaluate(loader_te.load(), steps=loader_te.steps_per_epoch)

print('Done.\n'
      f'Test loss: {eval_results[0]:2.f}\n'
      f'Test accuracy: {eval_results[1]:.2f}')

Epoch 1/1000
1/1 [==============================] - 0s 462ms/step - loss: 1.1087 - acc: 0.2833 - val_loss: 1.1010 - val_acc: 0.6500
Epoch 2/1000
1/1 [==============================] - 0s 89ms/step - loss: 1.1005 - acc: 0.6167 - val_loss: 1.0974 - val_acc: 0.7500
Epoch 3/1000
1/1 [==============================] - 0s 91ms/step - loss: 1.0946 - acc: 0.7500 - val_loss: 1.0928 - val_acc: 0.7600
Epoch 4/1000
1/1 [==============================] - 0s 101ms/step - loss: 1.0894 - acc: 0.8833 - val_loss: 1.0872 - val_acc: 0.7560
Epoch 5/1000
1/1 [==============================] - 0s 93ms/step - loss: 1.0805 - acc: 0.8167 - val_loss: 1.0809 - val_acc: 0.7520
Epoch 6/1000
1/1 [==============================] - 0s 98ms/step - loss: 1.0727 - acc: 0.8667 - val_loss: 1.0744 - val_acc: 0.7580
Epoch 7/1000
1/1 [==============================] - 0s 95ms/step - loss: 1.0636 - acc: 0.9000 - val_loss: 1.0681 - val_acc: 0.7520
Epoch 8/1000
1/1 [==============================] - 0s 105ms/step - loss: 1.0563 